In [1]:
#imports
import sys, os, numpy, pandas, cv2, csv, operator, json
from time import sleep
from tqdm import tnrange, tqdm_notebook
import tensorflow as tf

#-----------Keras
from keras.models import Sequential
from keras.layers import Convolution2D
from keras.layers import MaxPooling2D
from keras.layers import Flatten
from keras.layers import Dense
from keras.preprocessing.image import ImageDataGenerator
from IPython.display import display
from PIL import Image

#https://medium.com/nybles/create-your-first-image-recognition-classifier-using-cnn-keras-and-tensorflow-backend-6eaab98d14dd

Using TensorFlow backend.


In [2]:
#globals
path = "train_data/originals/"
graypath = "train_data/grayscale/"
csvpath = "train_data/train.csv"
image_set = []
label_set = []
petID_column = 21
adoptionspeed_column = 23
#create dictionary
pets = {}

##### makeDirectories() <br/>
_This method creates directories if needed for each petid denoted by the image filenames._

##### removeEmptyFolders() <br/>
_This method deletes empty folders inside of a specified folder path._

##### loadImages() <br/>
_This method reads in the original image files one by one, previewing a certain number of them if specified, resizing them all, converting them to grayscale, and saving them out if they don't already exist._

In [3]:
def makeDirectories():
    if not os.path.exists("train_data"):
        os.mkdir("train_data")
    if not os.path.exists(path):
        os.mkdir(path)
    if not os.path.exists(graypath):
        os.mkdir(graypath)
    
    valid_types = [".jpg",".gif",".png",".tga"]
    for f in tqdm_notebook(os.listdir(path), desc='Directory Labelling Progress'):
        ext = os.path.splitext(f)[1]
        if ext.lower() not in valid_types:
            return
        n = f.split("-")[0]
        label_set.append(n)
        if not os.path.exists(graypath + n + "/"):
            os.mkdir(graypath + n + "/")
            print("\rCreated Directory: " + graypath + n + "/", end='')
    return

In [4]:
def removeEmptyFolders(folderpath="train_data/grayscale/"):
    for folder in tqdm_notebook(os.listdir(folderpath), desc='Empty folder deletion Progress'):
        if os.path.exists(folderpath + folder):
            if next(os.scandir(folderpath + folder), None) is None:
                print("\rRemoving empty folder: " + folder + "\tfrom: " + folderpath)
                os.rmdir(folderpath + folder)
    return

In [5]:
def loadImages(img_preview=0, sizex=200, sizey=200):
    if not os.path.exists("train_data"):
        os.mkdir("train_data")
    if not os.path.exists(path):
        os.mkdir(path)
    if not os.path.exists(graypath):
        os.mkdir(graypath)
  
    valid_types = [".jpg",".gif",".png",".tga"]
    #i = 0
    for f in tqdm_notebook(os.listdir(path), desc='Grayscale Conversion Progress'):
        #i += 1
        #print(path + "/" + f)
        ext = os.path.splitext(f)[1]
        #print(f.splittext(f)[1])
        if ext.lower() not in valid_types:
            return
        #cimage = cv2.imread(path+"/"+f)
        n = f.split("-")[0]
        #label_set.append(n)
        
        if not os.path.isfile(graypath + n + "/" + f):
            image = cv2.imread(path+"/"+f, 0) #pass in 0 as second parameter to automatically convert to grayscale
            #image = cv2.cvtColor(cimage, cv2.COLOR_BGR2GRAY, 0, 0)
        
            if image is not None:
                image = cv2.resize(image, dsize=(sizex, sizey), interpolation = cv2.INTER_CUBIC)
                image_set.append(image)
                #print(image_set[i-1])
                #if i <= img_preview:
                #    cv2.imshow('color_image',cimage)
                #    cv2.imshow('gray_image',image) 
                #    cv2.waitKey(0)                 # Waits forever for user to press any key
                #    cv2.destroyAllWindows()        # Closes displayed windows
            
                if not os.path.isfile(graypath + n + "/" + f):
                    cv2.imwrite(graypath + n + "/" + f, image)
                    print("\rCreated File: " + graypath + n + "/" + f, end='')
    return

##### initial_image_processing() <br/>
_This method runs the previous 3 in a batch call in a specific order._

In [6]:
def initial_image_processing():
    #for i in tnrange(1, desc="initial image processing progress"):
    makeDirectories()
    loadImages()
    removeEmptyFolders()
    return

In [7]:
initial_image_processing()
#makeDirectories()
#loadImages()
#loadImages(2)

A Jupyter Widget

A Jupyter Widget

A Jupyter Widget

In [8]:
#words = ["hey-1.abc", "hey-2.abc", "hi-1.abc", "tuesday-12.abc"]
#for f in tqdm_notebook(words, desc='Conversion Progress'):
#    print(path + "/" + f)
    #a = "hello-2.txt"
#    ext = os.path.splitext(f)[1]
#    f = f.replace(ext,"")
#    #print(ext)
#    delim = (f)#[:-6] #.split("-")[0]
#    print(delim)

##### isEnglish() <br/>
_This method returns true if the passed in string is commonly used in the english alphabet._

##### readCSV() <br/>
_This method goes through each row in a csv file specified in the globals and matches their petid column with the petid labels we got from loading all of our images in. we then store the pet id and adoption speed into a pets dictionary. commented out is the code for printing all the rows of a specified column._

##### pandasCSV() <br/>
_This method creates reads in specified columns of the csv file, petid and adoptionspeed, and if the petid matches a label in the label set from earlier loading then we store them into a dictionary, I had problems using this and running out of memory or something on jupyter notebook, so I simply used the readCSV method, but this one compares faster as far as it seems._

In [9]:
def isEnglish(s):
    try:
        s.encode(encoding='utf-8').decode('ascii')
    except UnicodeDecodeError:
        return False
    else:
        return True

def readCSV(printout=None):
    with open(csvpath, 'r', encoding="utf-8") as csv_file:
        csv_reader= csv.reader(csv_file)
        
        #sorted_csv = sorted(csv_reader, key=operator.itemgetter(petID_column))
        label_set.sort()
        for line in tqdm_notebook(csv_reader, desc="csv label matching progress"):
            for l in label_set:
                if line[petID_column] == l:
                    if printout is not None:
                        print(line[petID_column] + ", " + l)
                    key = l
                    if not key in pets:
                        #pets.setdefault(key, []).append(l)
                        pets.setdefault(key, []).append(line[adoptionspeed_column])
        return pets
            #for l in label_set:
             #   if line[petID_column] == l:
                    #print (line[petID_column])
                    
        #return sorted_csv
        #for line in csv_reader:
        #    if isEnglish(line[petID_column]):
        #        print("eng: " + line[petID_column])
        #    else:
        #        temp = ''
        #        for parse in line[petID_column]:
        #            if isEnglish(parse):
        #                temp+=parse
        #        print("temp: " + temp)

def pandasCSV():
    #pandas alternative start to above
    with open(csvpath, 'r', encoding="utf-8") as csv_file:
        df = pandas.read_csv(csv_file, usecols=['PetID', 'AdoptionSpeed'])
        for l in tqdm_notebook(label_set, desc="csv label matching progress"):
            key = l
            pets.setdefault(key, []).append(df[df['PetID'] == l])
        
        #print(df[df['PetID'] == label_set[100]])

In [10]:
#pandasCSV()
#for l in label_set:
#    print(l)

In [11]:
readCSV()



A Jupyter Widget

{'0008c5398': ['3'],
 '000a290e4': ['2'],
 '000fb9572': ['3'],
 '0011d7c25': ['2'],
 '00156db4a': ['1'],
 '001a1aaad': ['2'],
 '001b1507c': ['1'],
 '002230dea': ['1'],
 '0025a8313': ['4'],
 '0038234c6': ['4'],
 '0038c9343': ['2'],
 '003dd2e26': ['2'],
 '0045ed62a': ['3'],
 '004a26127': ['3'],
 '004c2f355': ['1'],
 '0052dcf47': ['4'],
 '00553ae55': ['1'],
 '0058586f1': ['4'],
 '005afe792': ['2'],
 '005bb92d8': ['1'],
 '0063bd7e0': ['4'],
 '0063f83c9': ['1'],
 '00648f96f': ['2'],
 '006610fe3': ['4'],
 '006d301e9': ['3'],
 '006ffebaf': ['2'],
 '00709d75b': ['1'],
 '0073c33d0': ['3'],
 '007bc1db4': ['4'],
 '007ffeccd': ['2'],
 '00904fc2c': ['3'],
 '0090eb457': ['4'],
 '009239f92': ['3'],
 '00a1a8af4': ['2'],
 '00a1f270a': ['4'],
 '00ac364a4': ['4'],
 '00af25fc0': ['2'],
 '00b00d5c1': ['2'],
 '00b23513e': ['2'],
 '00be0a63e': ['1'],
 '00bfa5da9': ['4'],
 '00c19f4fa': ['2'],
 '00c71a320': ['4'],
 '00e50c7a7': ['1'],
 '00eca0391': ['4'],
 '00eced1f0': ['3'],
 '00f3a3993': ['2'],
 '00f63c6fc':

In [12]:
print(pets)
#print(pets.get(label_set[0]))
#pets.clear()

{'0008c5398': ['3'], '000a290e4': ['2'], '000fb9572': ['3'], '0011d7c25': ['2'], '00156db4a': ['1'], '001a1aaad': ['2'], '001b1507c': ['1'], '002230dea': ['1'], '0025a8313': ['4'], '0038234c6': ['4'], '0038c9343': ['2'], '003dd2e26': ['2'], '0045ed62a': ['3'], '004a26127': ['3'], '004c2f355': ['1'], '0052dcf47': ['4'], '00553ae55': ['1'], '0058586f1': ['4'], '005afe792': ['2'], '005bb92d8': ['1'], '0063bd7e0': ['4'], '0063f83c9': ['1'], '00648f96f': ['2'], '006610fe3': ['4'], '006d301e9': ['3'], '006ffebaf': ['2'], '00709d75b': ['1'], '0073c33d0': ['3'], '007bc1db4': ['4'], '007ffeccd': ['2'], '00904fc2c': ['3'], '0090eb457': ['4'], '009239f92': ['3'], '00a1a8af4': ['2'], '00a1f270a': ['4'], '00ac364a4': ['4'], '00af25fc0': ['2'], '00b00d5c1': ['2'], '00b23513e': ['2'], '00be0a63e': ['1'], '00bfa5da9': ['4'], '00c19f4fa': ['2'], '00c71a320': ['4'], '00e50c7a7': ['1'], '00eca0391': ['4'], '00eced1f0': ['3'], '00f3a3993': ['2'], '00f63c6fc': ['4'], '00f997463': ['4'], '010a59236': ['4'],

##### save_json() <br/>
_This method uses a specified or default filepath and filename as well as the pets dictionary, which can also be specified to save other variables out, such as lists or arrays. Using these, it simply saves out the data into a .json file._

##### load_json() <br/>
_This method uses a specified or default filepath and filename as well as the pets dictionary, which can also be specified to load and store the data into a different variable name or type, such as a list or an array. Using these it simply loads the data from a .json file._

In [13]:
def save_json(filepath="train_data/", filename="pets_dictionary.json", dictionary=pets):
    with open(filepath + filename, 'w') as file:
        json.dump(dictionary, file, sort_keys=True, indent=4)
    return
def load_json(filepath="train_data/", filename="pets_dictionary.json", dictionary=pets):
    with open(filepath + filename, 'r') as file:
        dictionary = json.load(file)
    return dictionary

In [14]:
save_json()
save_json(filename="label_set.json", dictionary=label_set)

In [15]:
test_load_pets_dictionary = {}
test_load_label_set = []

test_load_pets_dictionary = load_json(dictionary=test_load_pets_dictionary)
print(test_load_pets_dictionary)



{'0008c5398': ['3'], '000a290e4': ['2'], '000fb9572': ['3'], '0011d7c25': ['2'], '00156db4a': ['1'], '001a1aaad': ['2'], '001b1507c': ['1'], '002230dea': ['1'], '0025a8313': ['4'], '0038234c6': ['4'], '0038c9343': ['2'], '003dd2e26': ['2'], '0045ed62a': ['3'], '004a26127': ['3'], '004c2f355': ['1'], '0052dcf47': ['4'], '00553ae55': ['1'], '0058586f1': ['4'], '005afe792': ['2'], '005bb92d8': ['1'], '0063bd7e0': ['4'], '0063f83c9': ['1'], '00648f96f': ['2'], '006610fe3': ['4'], '006d301e9': ['3'], '006ffebaf': ['2'], '00709d75b': ['1'], '0073c33d0': ['3'], '007bc1db4': ['4'], '007ffeccd': ['2'], '00904fc2c': ['3'], '0090eb457': ['4'], '009239f92': ['3'], '00a1a8af4': ['2'], '00a1f270a': ['4'], '00ac364a4': ['4'], '00af25fc0': ['2'], '00b00d5c1': ['2'], '00b23513e': ['2'], '00be0a63e': ['1'], '00bfa5da9': ['4'], '00c19f4fa': ['2'], '00c71a320': ['4'], '00e50c7a7': ['1'], '00eca0391': ['4'], '00eced1f0': ['3'], '00f3a3993': ['2'], '00f63c6fc': ['4'], '00f997463': ['4'], '010a59236': ['4'],

In [16]:
test_load_label_set = load_json(filename="label_set.json", dictionary=test_load_label_set)
print(test_load_label_set)

['0008c5398', '0008c5398', '0008c5398', '0008c5398', '0008c5398', '0008c5398', '000a290e4', '000a290e4', '000fb9572', '000fb9572', '000fb9572', '000fb9572', '000fb9572', '000fb9572', '0011d7c25', '0011d7c25', '0011d7c25', '00156db4a', '00156db4a', '00156db4a', '00156db4a', '00156db4a', '001a1aaad', '001a1aaad', '001a1aaad', '001a1aaad', '001b1507c', '001b1507c', '001b1507c', '001b1507c', '001b1507c', '001b1507c', '002230dea', '002230dea', '002230dea', '002230dea', '002278114', '002278114', '002278114', '002278114', '002278114', '002278114', '002278114', '002278114', '002278114', '002278114', '002278114', '002278114', '002278114', '0025a8313', '0025a8313', '0038234c6', '0038234c6', '0038234c6', '0038c9343', '0038c9343', '0038c9343', '0038c9343', '0038c9343', '003dd2e26', '003dd2e26', '003dd2e26', '0045ed62a', '0045ed62a', '0045ed62a', '004709939', '004709939', '004709939', '004a26127', '004a26127', '004c2f355', '004c2f355', '0052dcf47', '0052dcf47', '0052dcf47', '00553ae55', '00553ae55'

In [17]:
tf.__version__

'1.10.0'

In [19]:
#initialize convolutional neural network CNN
classifier = Sequential()
#convolution
classifier.add(Convolution2D(32,3,3, input_shape=(64,64,3), activation='relu'))
#pooling
classifier.add(MaxPooling2D(pool_size=(2,2)))
#flattening
classifier.add(Flatten())
#full connection
classifier.add(Dense(output_dim=128, activation='relu'))
classifier.add(Dense(output_dim=1, activation='sigmoid'))
#compile CNN
classifier.compile(optimizer='adam', loss='binary_crossentropy', metrics=['accuracy'])

#fitting CNN to the images
train_datagen = ImageDataGenerator(
    rescale=1./255,
    shear_range=0.2,
    zoom_range=0.2,
    horizontal_flip=True
)

test_datagen = ImageDataGenerator(rescale=1./255)

training_set = train_datagen.flow_from_directory(
    graypath,
    target_size=(64,64),
    batch_size=32,
    class_mode='binary'
)

test_set = test_datagen.flow_from_directory(
    "train_data/grayscale_test",
    target_size=(64,64),
    batch_size=32,
    class_mode='binary'
)

classifier.fit_generator(
    training_set,
    steps_per_epoch=8000,
    epochs=10,
    validation_data=test_set,
    validation_steps=800
)

D:\Users\Sunfl\Anaconda3\lib\site-packages\ipykernel_launcher.py:4: UserWarning: Update your `Conv2D` call to the Keras 2 API: `Conv2D(32, (3, 3), input_shape=(64, 64, 3..., activation="relu")`
  after removing the cwd from sys.path.
D:\Users\Sunfl\Anaconda3\lib\site-packages\ipykernel_launcher.py:10: UserWarning: Update your `Dense` call to the Keras 2 API: `Dense(activation="relu", units=128)`
  # Remove the CWD from sys.path while we load stuff.
D:\Users\Sunfl\Anaconda3\lib\site-packages\ipykernel_launcher.py:11: UserWarning: Update your `Dense` call to the Keras 2 API: `Dense(activation="sigmoid", units=1)`
  # This is added back by InteractiveShellApp.init_path()


Found 52859 images belonging to 13221 classes.
Found 5452 images belonging to 1431 classes.
Epoch 1/10


 163/8000 [..............................] - ETA: 2:26:27 - loss: -337.9401 - acc: 0.0000e+0 - ETA: 1:20:52 - loss: -59150.0638 - acc: 0.0000e+0 - ETA: 58:52 - loss: -75548.1571 - acc: 0.0000e+00  - ETA: 48:13 - loss: -88967.8639 - acc: 0.0000e+0 - ETA: 41:43 - loss: -94476.8755 - acc: 0.0000e+0 - ETA: 37:23 - loss: -95014.9614 - acc: 0.0000e+0 - ETA: 34:28 - loss: -94913.0662 - acc: 0.0000e+0 - ETA: 32:10 - loss: -94445.6829 - acc: 0.0000e+0 - ETA: 30:21 - loss: -95092.0689 - acc: 0.0000e+0 - ETA: 28:47 - loss: -95500.6198 - acc: 0.0000e+0 - ETA: 27:31 - loss: -95867.4981 - acc: 0.0000e+0 - ETA: 26:25 - loss: -94480.4306 - acc: 0.0000e+0 - ETA: 25:37 - loss: -95634.8830 - acc: 0.0000e+0 - ETA: 24:55 - loss: -96619.1112 - acc: 0.0000e+0 - ETA: 24:23 - loss: -97095.9356 - acc: 0.0000e+0 - ETA: 23:50 - loss: -98071.1090 - acc: 0.0000e+0 - ETA: 23:26 - loss: -98071.4294 - acc: 0.0000e+0 - ETA: 23:00 - loss: -98490.2015 - acc: 0.0000e+0 - ETA: 22:39 - loss: -100084.9574 - acc: 0.0000e+ - E

 326/8000 [>.............................] - ETA: 17:35 - loss: -104068.2893 - acc: 0.0000e+ - ETA: 17:35 - loss: -104131.3771 - acc: 0.0000e+ - ETA: 17:34 - loss: -104257.1593 - acc: 0.0000e+ - ETA: 17:34 - loss: -104141.0195 - acc: 0.0000e+ - ETA: 17:33 - loss: -104240.8380 - acc: 0.0000e+ - ETA: 17:33 - loss: -104213.9290 - acc: 0.0000e+ - ETA: 17:33 - loss: -104197.7343 - acc: 0.0000e+ - ETA: 17:32 - loss: -104247.7973 - acc: 0.0000e+ - ETA: 17:32 - loss: -104188.8211 - acc: 0.0000e+ - ETA: 17:32 - loss: -104244.7470 - acc: 0.0000e+ - ETA: 17:32 - loss: -104297.5677 - acc: 0.0000e+ - ETA: 17:32 - loss: -104296.4432 - acc: 0.0000e+ - ETA: 17:31 - loss: -104252.9450 - acc: 0.0000e+ - ETA: 17:31 - loss: -104390.7368 - acc: 0.0000e+ - ETA: 17:30 - loss: -104453.2440 - acc: 0.0000e+ - ETA: 17:30 - loss: -104511.9885 - acc: 0.0000e+ - ETA: 17:30 - loss: -104443.5211 - acc: 0.0000e+ - ETA: 17:30 - loss: -104366.8783 - acc: 0.0000e+ - ETA: 17:29 - loss: -104351.0040 - acc: 0.0000e+ - ETA: 

 489/8000 [>.............................] - ETA: 17:10 - loss: -104209.0491 - acc: 9.5566e- - ETA: 17:10 - loss: -104218.3944 - acc: 9.5274e- - ETA: 17:09 - loss: -104228.1645 - acc: 9.4985e- - ETA: 17:09 - loss: -104213.0302 - acc: 9.4697e- - ETA: 17:09 - loss: -104193.8213 - acc: 9.4411e- - ETA: 17:09 - loss: -104165.7424 - acc: 9.4127e- - ETA: 17:09 - loss: -104158.0549 - acc: 9.3844e- - ETA: 17:09 - loss: -104156.3590 - acc: 9.3563e- - ETA: 17:08 - loss: -104161.4071 - acc: 9.3284e- - ETA: 17:09 - loss: -104123.2879 - acc: 9.3006e- - ETA: 17:08 - loss: -104132.5568 - acc: 9.2730e- - ETA: 17:08 - loss: -104145.5162 - acc: 9.2456e- - ETA: 17:07 - loss: -104110.8336 - acc: 9.2183e- - ETA: 17:07 - loss: -104095.7950 - acc: 9.1912e- - ETA: 17:07 - loss: -104059.4425 - acc: 9.1642e- - ETA: 17:07 - loss: -104018.8800 - acc: 9.1374e- - ETA: 17:07 - loss: -104046.2365 - acc: 9.1108e- - ETA: 17:07 - loss: -104021.5242 - acc: 9.0843e- - ETA: 17:07 - loss: -104017.8550 - acc: 9.0580e- - ETA: 

...

7335/8000 [==========================>...] - ETA: 1:45 - loss: -105014.0242 - acc: 3.0496e-0 - ETA: 1:45 - loss: -105014.5947 - acc: 3.0492e-0 - ETA: 1:45 - loss: -105015.7333 - acc: 3.0488e-0 - ETA: 1:45 - loss: -105014.7218 - acc: 3.0484e-0 - ETA: 1:44 - loss: -105017.7645 - acc: 3.0479e-0 - ETA: 1:44 - loss: -105016.3677 - acc: 3.0475e-0 - ETA: 1:44 - loss: -105017.5290 - acc: 3.0471e-0 - ETA: 1:44 - loss: -105018.2707 - acc: 3.0467e-0 - ETA: 1:44 - loss: -105015.1153 - acc: 3.0462e-0 - ETA: 1:44 - loss: -105015.6478 - acc: 3.0458e-0 - ETA: 1:44 - loss: -105015.7041 - acc: 3.0454e-0 - ETA: 1:44 - loss: -105016.2825 - acc: 3.0450e-0 - ETA: 1:43 - loss: -105017.0096 - acc: 3.0445e-0 - ETA: 1:43 - loss: -105017.5289 - acc: 3.0441e-0 - ETA: 1:43 - loss: -105017.9857 - acc: 3.0437e-0 - ETA: 1:43 - loss: -105017.4678 - acc: 3.0433e-0 - ETA: 1:43 - loss: -105016.6019 - acc: 3.0428e-0 - ETA: 1:43 - loss: -105014.7505 - acc: 3.0424e-0 - ETA: 1:43 - loss: -105016.1616 - acc: 3.0420e-0 - ETA: 

7498/8000 [===========================>..] - ETA: 1:24 - loss: -104996.5175 - acc: 3.4079e-0 - ETA: 1:24 - loss: -104997.6099 - acc: 3.4074e-0 - ETA: 1:24 - loss: -104997.9503 - acc: 3.4069e-0 - ETA: 1:24 - loss: -104994.2285 - acc: 3.4065e-0 - ETA: 1:24 - loss: -104997.2458 - acc: 3.4060e-0 - ETA: 1:23 - loss: -104997.6388 - acc: 3.4055e-0 - ETA: 1:23 - loss: -104996.9941 - acc: 3.4051e-0 - ETA: 1:23 - loss: -104997.6931 - acc: 3.4046e-0 - ETA: 1:23 - loss: -104996.9034 - acc: 3.4041e-0 - ETA: 1:23 - loss: -104997.1876 - acc: 3.4037e-0 - ETA: 1:23 - loss: -104996.7277 - acc: 3.4032e-0 - ETA: 1:23 - loss: -104994.5660 - acc: 3.4027e-0 - ETA: 1:23 - loss: -104991.4289 - acc: 3.4023e-0 - ETA: 1:22 - loss: -104992.3271 - acc: 3.4018e-0 - ETA: 1:22 - loss: -104993.6162 - acc: 3.4014e-0 - ETA: 1:22 - loss: -104993.8973 - acc: 3.4009e-0 - ETA: 1:22 - loss: -104991.1437 - acc: 3.4004e-0 - ETA: 1:22 - loss: -104993.0741 - acc: 3.4000e-0 - ETA: 1:22 - loss: -104992.4756 - acc: 3.3995e-0 - ETA: 

7667/8000 [===========================>..] - ETA: 1:03 - loss: -104983.5445 - acc: 3.3338e-0 - ETA: 1:03 - loss: -104984.3612 - acc: 3.3333e-0 - ETA: 1:03 - loss: -104985.1678 - acc: 3.3329e-0 - ETA: 1:03 - loss: -104983.9755 - acc: 3.3324e-0 - ETA: 1:03 - loss: -104987.6289 - acc: 3.3320e-0 - ETA: 1:03 - loss: -104987.0680 - acc: 3.3316e-0 - ETA: 1:03 - loss: -104987.6194 - acc: 3.3311e-0 - ETA: 1:02 - loss: -104987.9988 - acc: 3.3307e-0 - ETA: 1:02 - loss: -104988.2444 - acc: 3.3302e-0 - ETA: 1:02 - loss: -104987.1944 - acc: 3.3298e-0 - ETA: 1:02 - loss: -104987.8637 - acc: 3.3293e-0 - ETA: 1:02 - loss: -104987.8690 - acc: 3.3289e-0 - ETA: 1:02 - loss: -104989.0609 - acc: 3.3285e-0 - ETA: 1:02 - loss: -104987.7695 - acc: 3.3280e-0 - ETA: 1:02 - loss: -104984.9921 - acc: 3.3276e-0 - ETA: 1:01 - loss: -104985.7917 - acc: 3.3271e-0 - ETA: 1:01 - loss: -104986.2800 - acc: 3.3267e-0 - ETA: 1:01 - loss: -104985.2084 - acc: 3.3262e-0 - ETA: 1:01 - loss: -104983.7123 - acc: 3.3258e-0 - ETA: 

7837/8000 [============================>.] - ETA: 42s - loss: -104960.7146 - acc: 3.2603e- - ETA: 42s - loss: -104964.7269 - acc: 3.2599e- - ETA: 42s - loss: -104963.7980 - acc: 3.2595e- - ETA: 41s - loss: -104963.0796 - acc: 3.2590e- - ETA: 41s - loss: -104959.8132 - acc: 3.2586e- - ETA: 41s - loss: -104958.9382 - acc: 3.2582e- - ETA: 41s - loss: -104958.1885 - acc: 3.2578e- - ETA: 41s - loss: -104957.8212 - acc: 3.2573e- - ETA: 41s - loss: -104957.6709 - acc: 3.2569e- - ETA: 41s - loss: -104958.1189 - acc: 3.2565e- - ETA: 41s - loss: -104957.4006 - acc: 3.2561e- - ETA: 40s - loss: -104956.1596 - acc: 3.2556e- - ETA: 40s - loss: -104955.6706 - acc: 3.2552e- - ETA: 40s - loss: -104955.0851 - acc: 3.2548e- - ETA: 40s - loss: -104955.7906 - acc: 3.2544e- - ETA: 40s - loss: -104956.0279 - acc: 3.2539e- - ETA: 40s - loss: -104956.6069 - acc: 3.2535e- - ETA: 40s - loss: -104956.5060 - acc: 3.2531e- - ETA: 39s - loss: -104957.3738 - acc: 3.2527e- - ETA: 39s - loss: -104957.4219 - acc: 3.2522

8000/8000 [==============================] - ETA: 20s - loss: -104941.7742 - acc: 3.1896e- - ETA: 20s - loss: -104942.9810 - acc: 3.1892e- - ETA: 20s - loss: -104939.8175 - acc: 3.1888e- - ETA: 20s - loss: -104938.8226 - acc: 3.1884e- - ETA: 20s - loss: -104935.7960 - acc: 3.1880e- - ETA: 19s - loss: -104935.0759 - acc: 3.1876e- - ETA: 19s - loss: -104934.7960 - acc: 3.1871e- - ETA: 19s - loss: -104937.4171 - acc: 3.1867e- - ETA: 19s - loss: -104937.2002 - acc: 3.1863e- - ETA: 19s - loss: -104937.0687 - acc: 3.1859e- - ETA: 19s - loss: -104938.2915 - acc: 3.1855e- - ETA: 19s - loss: -104938.4809 - acc: 3.1851e- - ETA: 19s - loss: -104939.7467 - acc: 3.1847e- - ETA: 18s - loss: -104939.5343 - acc: 3.1843e- - ETA: 18s - loss: -104938.0471 - acc: 3.1839e- - ETA: 18s - loss: -104937.8099 - acc: 3.1835e- - ETA: 18s - loss: -104938.0731 - acc: 3.1831e- - ETA: 18s - loss: -104938.6120 - acc: 3.1827e- - ETA: 18s - loss: -104939.9237 - acc: 3.1823e- - ETA: 18s - loss: -104939.4203 - acc: 3.1819

In [21]:
#https://keras.io/getting-started/faq/#how-can-i-save-a-keras-model
#https://stackoverflow.com/questions/51628450/how-to-save-a-trained-model-in-keras-to-use-it-in-an-application
#https://machinelearningmastery.com/save-load-keras-deep-learning-models/
from keras.models import model_from_json   
# serialize model to JSON
model_json = classifier.to_json()
with open("model.json", "w") as json_file:
    json_file.write(model_json)
# serialize weights to HDF5
classifier.save_weights("model.h5")
print("Saved model to disk")

Saved model to disk
